# Data Collection

#### We collect tweets regarding the **META** (ticker:`META`) company using StockTwits API. 

### Seup the environement

In [1]:
#!pip install "pymongo[srv]"==3.11
#!pip install pymongo --upgrade
#!pip install openai

### Import libs

In [1]:
#### COMMON ####
import pandas as pd
import numpy as np

import json
import requests
from datetime import datetime

### MONGO DB ####
from pymongo.mongo_client import MongoClient

### Import utils function ###S
from utils import test_connection_db, collect_tweets, insert_tweets, get_tweets_from_db, URI, DB_NAME

### STEP 1: Load `META` tweets from StockTwits

In [2]:
df_meta_tweets = collect_tweets(ticker="AAPL", nb_url=70000)
df_meta_tweets

STARTING TO COLLECT TWEET AAPL...


COLLECTNG FROM:... 1: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547231032
30
COLLECTNG FROM:... 2: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547222391
60
COLLECTNG FROM:... 3: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547214836
90
COLLECTNG FROM:... 4: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547204132
120
COLLECTNG FROM:... 5: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547191614
150
COLLECTNG FROM:... 6: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547186749
180
COLLECTNG FROM:... 7: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547177035
209
COLLECTNG FROM:... 8: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547169018
239
COLLECTNG FROM:... 9: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=547164122
268
COLLECTNG FROM:... 10: https://api.stocktwits.com/api/2/streams/symbol/AAPL.json?max=

#### NOTE:

* The sentiment given by StockTwits will be the label (ground truth) of our data

### Data Cleansing

In [ ]:
### TO DO build a function to clean the tweet

import pandas as pd
import glob 

files = glob.glob('aapl_tweets_*.xlsx')

dfs = []

for f in files:
    dfs.append(pd.read_excel(f))

dfs = pd.concat(dfs)

import regex as re

def rep(text):
    text = str(text)

    return re.sub('&#39;', '\'', text)

dfs['content'] =  dfs['content'].apply(rep)

for i in range(0, len(dfs) // 50000 + 1):

    insert_many_to_mongodb(dfs.iloc[i*50000: (i+1) * 50000], URI, DB_NAME, 'AAPL')


### Store the tweets collection into the DB

##### Test the connection with the MongoDB cluster

### Extract data from the MongoDB database

In [8]:
# Retrieve data from MongoDB
data_from_mongodb = get_tweets_from_db(uri=URI, db_name=DB_NAME, collection_name="APPL")

# Create DataFrame from retrieved data
df = pd.DataFrame(data_from_mongodb)
df = pd.concat([pd.DataFrame(d) for d in df])

df

_id                  date  \
0    65f960bafd8bcf53d7bc88a8  2024-03-19T08:06:15Z   
1    65f960bbfd8bcf53d7bc88aa  2024-03-19T04:44:30Z   
2    65f960bdfd8bcf53d7bc88ac  2024-03-19T04:25:32Z   
3    65f960befd8bcf53d7bc88ae  2024-03-19T04:17:06Z   
4    65f960c0fd8bcf53d7bc88b0  2024-03-19T03:23:11Z   
..                        ...                   ...   
100  65f96164fd8bcf53d7bc8970  2024-03-15T19:52:59Z   
101  65f96166fd8bcf53d7bc8972  2024-03-15T19:32:07Z   
102  65f96168fd8bcf53d7bc8974  2024-03-15T19:17:57Z   
103  65f9616afd8bcf53d7bc8976  2024-03-15T18:51:51Z   
104  65f9616cfd8bcf53d7bc8978  2024-03-15T18:48:11Z   

                                               content true_sentiment  
0    $VERB  \n$META  \n \nMETA partnership!  \n \n“...        bullish  
1    $RBLX $META \nzuck should buy this and add it ...        bullish  
2    $TSLA Lower Weekly low \nunder Week Low 3-11-2...        bearish  
3    $SPY let’s buy TikTok make it a America Compan...        bullish  
4    $META https://www.reuters.com/legal/transactio...        bearish  
..                                                 ...            ...  
100  $SPY You thought MM and Imbalances were going ...        bearish  
101  $META ops, Marky Mark ought to consider anothe...        bearish  
102  $META wow  Piss porr price action today, Im on...        bearish  
103  $META  at.  90.  All through towel, see now\n\...        bullish  
104  $META  \n \nJust doubled this at 483.94... rip...        bullish  

[105 rows x 4 columns]